# PySpark - Pandas UDF. Скалярные типы функций (SCALAR, SCALAR_ITER) 
В данном Notebook рассматриваются типы функций: **SCALAR**, **SCALAR_ITER**

| Тип | Скалярные/Групповые | Возвращаемое значение | Трансормация |
|:----|:-----|:------|:--------------|
| **SCALAR** | Скалярные | Series | Поэлементные преобразования (скалярные вычисления) |
| **SCALAR_ITER** | Скалярные | Iterator[Series] | Батчевые преобразования (скалярные вычисления) |

### Описание  
```python
pyspark.sql.functions.pandas_udf (f=None, returnType=None, functionType=None)
#    f=None,            - Функция для преобразования в UDF
#    returnType=None,   - Тип возвращаемого значения
#    functionType=None  - Тип UDF (depricted)
```
**Тип функций:** *SCALAR*, *SCALAR_ITER*

### Параметр `returnType` (Строковые обозначения):
```python
# Примитивные типы
@pandas_udf("int")      # IntegerType
@pandas_udf("long")     # LongType  
@pandas_udf("float")    # FloatType
@pandas_udf("double")   # DoubleType
@pandas_udf("string")   # StringType
@pandas_udf("boolean")  # BooleanType
@pandas_udf("date")     # DateType
@pandas_udf("timestamp") # TimestampType

# Сложные типы
@pandas_udf("array<int>")           # ArrayType(IntegerType())
@pandas_udf("map<string,int>")      # MapType(StringType(), IntegerType())
@pandas_udf("struct<name:string,age:int>") # StructType
```

In [1]:
# БД для тестовых DataSet 
DATA_DB = "pandas_udf_db"

In [2]:
import os
import sys
spark_home = os.environ.get('SPARK_HOME', None)
sys.path.insert(0, spark_home + "python")
os.environ["SPARK_LOCAL_IP"]='localhost'
from pyspark import SparkContext, SparkConf#, HiveContext
conf = SparkConf()\
             .setAppName("Example Spark")\
             .setMaster("local[2]")\
             .setAppName("CountingSheep")\
             .set("spark.sql.catalogImplementation", "hive")
sc = SparkContext(conf=conf)
sc.setLogLevel("ERROR")

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
25/11/24 01:52:51 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


In [3]:
exec(open(os.path.join(spark_home, 'python/pyspark/shell.py')).read())

Welcome to
      ____              __
     / __/__  ___ _____/ /__
    _\ \/ _ \/ _ `/ __/  '_/
   /__ / .__/\_,_/_/ /_/\_\   version 3.5.7
      /_/

Using Python version 3.13.7 (main, Aug 20 2025 22:17:40)
Spark context Web UI available at http://localhost:4040
Spark context available as 'sc' (master = local[2], app id = local-1763938371638).
SparkSession available as 'spark'.


In [4]:
spark

In [5]:
from pyspark.sql.types import *
import pyspark.sql.functions as f_
from pyspark.sql import Window
from pyspark.sql import DataFrame, types
from pyspark.sql.functions import col, udf, pandas_udf
from datetime import datetime, date
from pyspark.sql import Row
import pandas as pd

## Предварительная подготовка
 - создание БД
 - создание DataSet

In [6]:
spark.sql(f"drop database if exists {DATA_DB} cascade")
spark.sql(f"create database {DATA_DB}")
spark.sql("show databases").show()

+-------------+
|    namespace|
+-------------+
|      default|
|  my_local_db|
|pandas_udf_db|
+-------------+



### Тестовый DataSet

In [7]:
# Save DataSet
spark.createDataFrame([
   Row(rowid=1,  double_value1=1.75, double_value2=70.0, str_value='Hello, World!!!',  date_value=date(2003, 6, 1), timestamp_value=datetime(2003, 1, 1, 12, 0)),
   Row(rowid=2,  double_value1=1.80, double_value2=80.0, str_value='Python@#$%^&*()',  date_value=date(2004, 6, 2), timestamp_value=datetime(2004, 1, 2, 15, 15)),
   Row(rowid=3,  double_value1=1.65, double_value2=60.0, str_value='Привет, мир!!! 123', date_value=date(2006, 4, 3), timestamp_value=datetime(2006, 1, 3, 19, 23)),
   Row(rowid=4,  double_value1=1.60, double_value2=60.0, str_value=None,       date_value=date(2007, 4, 10), timestamp_value=datetime(2007, 1, 7, 20, 44)),
   Row(rowid=5,  double_value1=1.70, double_value2=90.0, str_value='код (130) Номер 244=-55-56")', date_value=date(2008, 4, 10), timestamp_value=datetime(2008, 1, 9, 21, 34)),    
   Row(rowid=6,  double_value1=1.90, double_value2=90.0, str_value="## Ключевые особенности 'SCALAR UDF:'", date_value=date(2009, 4, 10), timestamp_value=datetime(2009, 4, 5, 23, 53)),
   Row(rowid=7,  double_value1=1.97, double_value2=100.0, str_value="**Векто(р)и'\зованные опе%%%рации**", date_value=date(2010, 4, 10), timestamp_value=datetime(2010, 8, 23, 10, 30)), 
   Row(rowid=8,  double_value1=1.96, double_value2=110.0, str_value="?*;'';&()_",   date_value=date(2011, 4, 10), timestamp_value=datetime(2011, 2, 5, 9, 19)), 
   Row(rowid=9,  double_value1=1.83, double_value2=71.0, str_value="Simple String №1",   date_value=date(2014, 5, 20), timestamp_value=datetime(2015, 12, 5, 19, 19)), 
   Row(rowid=10, double_value1=1.64, double_value2=87.0, str_value="Simple String №2",   date_value=date(2015, 5, 20), timestamp_value=datetime(2016, 1, 15, 19, 10))
]).write.format("parquet").mode("overwrite").saveAsTable(f"{DATA_DB}.table_for_scalar")

spark.sql(f"show tables from {DATA_DB}").show()

+-------------+----------------+-----------+
|    namespace|       tableName|isTemporary|
+-------------+----------------+-----------+
|pandas_udf_db|table_for_scalar|      false|
+-------------+----------------+-----------+



## PANDAS_UDF. SCALAR Example

### Особенности SCALAR UDF:

1. **Векторизованные операции** - работает с pandas Series, а не с отдельными значениями
2. **Высокая производительность** - использует Apache Arrow для быстрой передачи данных
3. **Простота использования** - знакомый pandas API
4. **Type safety** - строгая типизация входных и выходных данных
   
**Пример определения:**
```python
from pyspark.sql.functions import PandasUDFType
# устаревший синтаксис @pandas_udf(IntegerType(), PandasUDFType.SCALAR)
@pandas_udf("int")
def slen(s):
    return s.str.len()
``` 

In [8]:
import pyarrow as pa
print(f"PyArrow version: {pa.__version__}")

PyArrow version: 22.0.0


**Тестовый DataSet**

In [9]:
dfData = spark.table(f"{DATA_DB}.table_for_scalar")

In [10]:
dfData.dtypes

[('rowid', 'bigint'),
 ('double_value1', 'double'),
 ('double_value2', 'double'),
 ('str_value', 'string'),
 ('date_value', 'date'),
 ('timestamp_value', 'timestamp')]

In [11]:
dfData.orderBy("rowid").show()

+-----+-------------+-------------+--------------------+----------+-------------------+
|rowid|double_value1|double_value2|           str_value|date_value|    timestamp_value|
+-----+-------------+-------------+--------------------+----------+-------------------+
|    1|         1.75|         70.0|     Hello, World!!!|2003-06-01|2003-01-01 12:00:00|
|    2|          1.8|         80.0|     Python@#$%^&*()|2004-06-02|2004-01-02 15:15:00|
|    3|         1.65|         60.0|  Привет, мир!!! 123|2006-04-03|2006-01-03 19:23:00|
|    4|          1.6|         60.0|                NULL|2007-04-10|2007-01-07 20:44:00|
|    5|          1.7|         90.0|код (130) Номер 2...|2008-04-10|2008-01-09 21:34:00|
|    6|          1.9|         90.0|## Ключевые особе...|2009-04-10|2009-04-05 23:53:00|
|    7|         1.97|        100.0|**Векто(р)и'\зова...|2010-04-10|2010-08-23 10:30:00|
|    8|         1.96|        110.0|          ?*;'';&()_|2011-04-10|2011-02-05 09:19:00|
|    9|         1.83|         71

### 1. Простая функция с одним входным параметром

In [12]:
# Возведение значения в степень (квадрат)
@pandas_udf("double")
def square_value(series: pd.Series) -> pd.Series:
    """Вычисляет квадрат числа"""
    return (series ** 2).round(6)
# Применение
result = dfData.select("rowid", col("double_value1").alias("value"), square_value(col("double_value1")).alias("squared_value"))
result.orderBy("rowid").show()

[Stage 2:>                                                          (0 + 2) / 2]

+-----+-----+-------------+
|rowid|value|squared_value|
+-----+-----+-------------+
|    1| 1.75|       3.0625|
|    2|  1.8|         3.24|
|    3| 1.65|       2.7225|
|    4|  1.6|         2.56|
|    5|  1.7|         2.89|
|    6|  1.9|         3.61|
|    7| 1.97|       3.8809|
|    8| 1.96|       3.8416|
|    9| 1.83|       3.3489|
|   10| 1.64|       2.6896|
+-----+-----+-------------+



### 2. UDF с несколькими входными параметрами

In [13]:
@pandas_udf("double")
def calculate_bmi(height: pd.Series, weight: pd.Series) -> pd.Series:
    """Вычисляет индекс массы тела"""
    return (weight / (height ** 2)).round(2)

# Применение
result = dfData.select(
    "rowid", col("double_value1").alias("height"), col("double_value2").alias("weight"),
    calculate_bmi(col("height"), col("weight")).alias("bmi")
)
result.orderBy("rowid").show()

+-----+------+------+-----+
|rowid|height|weight|  bmi|
+-----+------+------+-----+
|    1|  1.75|  70.0|22.86|
|    2|   1.8|  80.0|24.69|
|    3|  1.65|  60.0|22.04|
|    4|   1.6|  60.0|23.44|
|    5|   1.7|  90.0|31.14|
|    6|   1.9|  90.0|24.93|
|    7|  1.97| 100.0|25.77|
|    8|  1.96| 110.0|28.63|
|    9|  1.83|  71.0| 21.2|
|   10|  1.64|  87.0|32.35|
+-----+------+------+-----+



### 3. UDF со строковыми преобразованиями

In [14]:
import re

# Тестовые данные с "грязным" текстом
@pandas_udf("string")
def clean_text(text_series: pd.Series) -> pd.Series:
    """Очистка текста от специальных символов"""
    def clean_string(text):
        if text is None:
            return None
        # Удаляем все кроме букв, цифр и пробелов
        return re.sub(r'[^a-zA-Zа-яА-Я0-9\s]', '', str(text)).strip()
    return text_series.apply(clean_string)

result = dfData.select("rowid", "str_value", clean_text(col("str_value")).alias("cleaned_value"))
result.orderBy("rowid").show(truncate=False)

+-----+-------------------------------------+-------------------------------+
|rowid|str_value                            |cleaned_value                  |
+-----+-------------------------------------+-------------------------------+
|1    |Hello, World!!!                      |Hello World                    |
|2    |Python@#$%^&*()                      |Python                         |
|3    |Привет, мир!!! 123                   |Привет мир 123                 |
|4    |NULL                                 |NULL                           |
|5    |код (130) Номер 244=-55-56")         |код 130 Номер 2445556          |
|6    |## Ключевые особенности 'SCALAR UDF:'|Ключевые особенности SCALAR UDF|
|7    |**Векто(р)и'\зованные опе%%%рации**  |Векторизованные операции       |
|8    |?*;'';&()_                           |                               |
|9    |Simple String №1                     |Simple String 1                |
|10   |Simple String №2                     |Simple String 2    

### 4. Математические вычисления

**Сложные математические вычисления** - сложная нелинейная функция
```
f(x) = log(x + 1) × √x + sin(x)

где:
ln — натуральный логарифм (основание e)
√x — квадратный корень от x
sin(x) — синус от x (в радианах)
```

**Z-score нормализация** — метод масштабирования данных, который преобразует значения так, чтобы они имели среднее значение 0 и стандартное отклонение 1.
```
Z = (X - μ) / σ

где:
Z = нормализованное значение (z-score)
X = исходное значение
μ = среднее значение выборки
σ = стандартное отклонение выборки
```

In [15]:
import numpy as np

@pandas_udf("double")
def complex_calculation(series: pd.Series) -> pd.Series:
    """Сложные математические вычисления"""
    return np.log(series + 1) * np.sqrt(series) + np.sin(series)

@pandas_udf("double")
def normalize_zscore(series: pd.Series) -> pd.Series:
    """Z-score нормализация"""
    mean_val = series.mean()
    std_val = series.std()
    return (series - mean_val) / std_val

# Применение
data = [(i, float(i * 10 + np.random.randn())) for i in range(1, 11)]
df = spark.createDataFrame(data, ["rowid", "value"])

result = df.select(
    "rowid", "value",
    complex_calculation(col("value")).alias("complex_result"),
    normalize_zscore(col("value")).alias("normalized")
)
result.show()

+-----+------------------+------------------+--------------------+
|rowid|             value|    complex_result|          normalized|
+-----+------------------+------------------+--------------------+
|    1| 7.633848086623447| 6.931915412109414| -1.3178039274747186|
|    2| 19.63043603684251|14.114375789802963| -0.5889668626372133|
|    3| 30.35742372817577| 18.11197589773293|  0.0627372932395931|
|    4|  39.1377644150771|24.090488317751817|  0.5961754475772716|
|    5| 49.86439732702725|27.355261373775036|  1.2478580492950684|
|    6| 60.36459461143597|31.361214968157338| -1.2428503710919487|
|    7| 70.29006072186735|36.694833401899245| -0.6220892842666597|
|    8|  79.5882041210142|38.291766820078315|-0.04056237785309997|
|    9| 89.80374339165094| 43.69083588183888|  0.5983405401148777|
|   10|101.13721531265449| 47.09527394032048|  1.3071614930968318|
+-----+------------------+------------------+--------------------+



### 5. Обработка дат

In [16]:
from datetime import datetime

@pandas_udf("string")
def format_date(date_series: pd.Series) -> pd.Series:
    """Форматирование даты"""
    return pd.to_datetime(date_series).dt.strftime('%Y-%m-%d %A')

@pandas_udf("int")
def days_since_epoch(date_series: pd.Series) -> pd.Series:
    """Количество дней с начала эпохи"""
    epoch = pd.Timestamp('1970-01-01')
    return (pd.to_datetime(date_series) - epoch).dt.days

# Тестовые данные
from datetime import date, timedelta
dates_data = [
    (1, date.today()),
    (2, date.today() - timedelta(days=30)),
    (3, date.today() + timedelta(days=15))
]
df = spark.createDataFrame(dates_data, ["rowid", "date"])

result = dfData.select(
    "rowid", "date_value",
    format_date(col("date_value")).alias("formatted_date"),
    days_since_epoch(col("date_value")).alias("days_since_epoch")
)
result.orderBy("rowid").show(truncate=False)

+-----+----------+--------------------+----------------+
|rowid|date_value|formatted_date      |days_since_epoch|
+-----+----------+--------------------+----------------+
|1    |2003-06-01|2003-06-01 Sunday   |12204           |
|2    |2004-06-02|2004-06-02 Wednesday|12571           |
|3    |2006-04-03|2006-04-03 Monday   |13241           |
|4    |2007-04-10|2007-04-10 Tuesday  |13613           |
|5    |2008-04-10|2008-04-10 Thursday |13979           |
|6    |2009-04-10|2009-04-10 Friday   |14344           |
|7    |2010-04-10|2010-04-10 Saturday |14709           |
|8    |2011-04-10|2011-04-10 Sunday   |15074           |
|9    |2014-05-20|2014-05-20 Tuesday  |16210           |
|10   |2015-05-20|2015-05-20 Wednesday|16575           |
+-----+----------+--------------------+----------------+



### 6. Условная логика

In [17]:
@pandas_udf("string")
def categorize_value(series: pd.Series) -> pd.Series:
    """Категоризация значений"""
    def categorize(value):
        if value < 10:
            return "Low"
        elif value < 50:
            return "Medium"
        else:
            return "High"
    
    return series.apply(categorize)

@pandas_udf("boolean")
def is_outlier(series: pd.Series) -> pd.Series:
    """Определение выбросов (значения вне 2 стандартных отклонений)"""
    mean_val = series.mean()
    std_val = series.std()
    return (series - mean_val).abs() > 2 * std_val

# Применение
data = [(i, float(i * 5 + np.random.randn() * 10)) for i in range(1, 21)]
df = spark.createDataFrame(data, ["id", "value"])

result = df.select(
    "id", "value",
    categorize_value(col("value")).alias("category"),
    is_outlier(col("value")).alias("is_outlier")
)
result.show()

+---+------------------+--------+----------+
| id|             value|category|is_outlier|
+---+------------------+--------+----------+
|  1|17.420890735251827|  Medium|     false|
|  2|-7.911544230053018|     Low|     false|
|  3| 21.36359796022306|  Medium|     false|
|  4|16.344851248480207|  Medium|     false|
|  5|25.044734212610166|  Medium|     false|
|  6|15.502907497227646|  Medium|     false|
|  7| 37.12591230005707|  Medium|     false|
|  8|47.568799576105974|  Medium|     false|
|  9| 46.79037703179671|  Medium|     false|
| 10| 40.11072140701947|  Medium|     false|
| 11| 48.34244629127504|  Medium|     false|
| 12| 66.31042000044721|    High|     false|
| 13| 76.95820937948123|    High|     false|
| 14| 71.47973439169178|    High|     false|
| 15| 73.30438954018493|    High|     false|
| 16| 61.00725638915016|    High|     false|
| 17| 76.28403482533022|    High|     false|
| 18|104.83688550888407|    High|     false|
| 19|109.45354370820421|    High|     false|
| 20| 88.5

### 7. Сравнение производительности UDF - Pandas UDF
Произодится генерация 300000 строк, к которым применяется последовательно UDF и Pandas UDF, содержащие идентичное преобразование (возведение числа в квадрат )


In [18]:
# Обычная UDF (медленная)
@udf(returnType=DoubleType())
def slow_square(value):
    return float(value ** 2)

# Pandas UDF (быстрая)
@pandas_udf("double")
def fast_square(series: pd.Series) -> pd.Series:
    return series ** 2

# Большой датасет для тестирования
large_data = [(i, float(i)) for i in range(300000)]
large_df = spark.createDataFrame(large_data, ["id", "value"])

**Сравнение производительности**

In [19]:
import time

# Pandas UDF
start = time.time()
result_pandas = large_df.select("id", fast_square(col("value")).alias("squared"))
result_pandas.count()  # Trigger execution
pandas_time = time.time() - start
print(f"Pandas UDF time: {pandas_time:.2f} seconds")

result_pandas = large_df.select("id", slow_square(col("value")).alias("squared"))
result_pandas.count()  # Trigger execution
pandas_time = time.time() - start
print(f"UDF time: {pandas_time:.2f} seconds")


Pandas UDF time: 0.42 seconds
UDF time: 0.57 seconds


### **SCALAR** используется, если:
- Данные помещаются в память
- Простые преобразования без предыдущих состояний
- Не требуется инициализация дорогих ресурсов

## PANDAS_UDF.SCALAR_ITER Example

### Особенности SCALAR_ITER UDF (в дополнение к особенностям SCALAR):

1. **Батчевая обработка данных** - Данные поступают **частями**, а не все сразу
2. **Стабильность** - Размер батча контролируется Spark (обычно тысячи записей)
3. **Масштабируемость** - Позволяет обрабатывать **очень большие датасеты**
4. **Управление памятью** - В памяти одновременно только один батч
5. **Накопительные вычисления** - Использует накопленную информацию (возможность кэширования)
6. **Потоковые агрегации** - Можно производить вычисления по окну
7. **Обработка ошибок** -  Можно обраатывать ошибки на уровне батчей

**Тестовые данные**

In [30]:
sampleData = [(i, float(i)) for i in range(1, 3560001)]  # 3000 записей

In [31]:
# Тестовые данные
#sampleData = [(i, float(i)) for i in range(1, 10160001)]  # 3000 записей
dfSample = spark.createDataFrame(sampleData, ["rowid", "value"]).repartition(6)

### 1. Базовый пример SCALAR_ITER
Общий принцип организации батчей

In [32]:
from typing import Iterator

# SCALAR - работает с отдельными Series
@pandas_udf("double")
def scalarudf(series: pd.Series) -> pd.Series:
    print(f"Обрабатывается {len(series)} строк сразу")
    return series ** 2

# SCALAR_ITER Pandas UDF с вызовом итератора в теле функции
@pandas_udf("double")
def process_batches(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
    """Обрабатывает данные батчами для экономии памяти"""
    batch_count = 0
    total_rows = 0
    for  i, batch in enumerate(iterator):
        # Обработка каждого батча
        print(f"Обрабатывается батч {i} размером: {len(batch)}")
        total_rows += len(batch)
        batch_count += 1
        yield batch ** 2
    print(f"Всего обработано {total_rows} строк в {batch_count} батчах")        

In [35]:
# Настройки, влияющие на размер батчей
spark.conf.set("spark.sql.execution.arrow.maxRecordsPerBatch", "100")
spark.conf.set("spark.sql.execution.arrow.pyspark.enabled", "true")

In [33]:
print(f"Размеры partitions: {dfSample.rdd.glom().map(len).collect()}")

[Stage 33:======================================>                   (4 + 2) / 6]

Размеры partitions: [593334, 593333, 593332, 593333, 593334, 593334]


**SCALAR**

In [37]:
result = dfSample.select("rowid", scalarudf(col("value")).alias("squared"))
f = result.collect()

Обрабатывается 100 строк сразу                                      (0 + 2) / 2]
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 строк сразу
Обрабатывается 100 с

**SCALAR_ITER**

In [36]:
result = dfSample.select("rowid", process_batches(col("value")).alias("squared"))
f = result.collect()

Обрабатывается батч 0 размером: 100                                 (0 + 2) / 2]
Обрабатывается батч 1 размером: 100
Обрабатывается батч 2 размером: 100
Обрабатывается батч 3 размером: 100
Обрабатывается батч 4 размером: 100
Обрабатывается батч 5 размером: 100
Обрабатывается батч 6 размером: 100
Обрабатывается батч 7 размером: 100
Обрабатывается батч 8 размером: 100
Обрабатывается батч 9 размером: 100
Обрабатывается батч 10 размером: 100
Обрабатывается батч 11 размером: 100
Обрабатывается батч 12 размером: 100
Обрабатывается батч 13 размером: 100
Обрабатывается батч 14 размером: 100
Обрабатывается батч 15 размером: 100
Обрабатывается батч 16 размером: 100
Обрабатывается батч 17 размером: 100
Обрабатывается батч 18 размером: 100
Обрабатывается батч 19 размером: 100
Обрабатывается батч 20 размером: 100
Обрабатывается батч 0 размером: 100
Обрабатывается батч 21 размером: 100
Обрабатывается батч 22 размером: 100
Обрабатывается батч 23 размером: 100
Обрабатывается батч 1 размером: 100
Обраб

### 2. Обработка с состоянием между батчами

In [200]:
@pandas_udf("double")
def running_statistics(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
    """Вычисляет статистики с накоплением между батчами"""
    running_sum = 0
    running_count = 0
    
    for batch in iterator:
        running_sum += batch.sum()
        running_count += len(batch)
        print(f"Обрабатывается батч размером: {len(batch)}")                    
        print(f"running_sum = {running_sum}, running_count = {running_count}")
        # Возвращаем среднее значение на текущий момент
        current_mean = running_sum / running_count
        yield pd.Series([current_mean] * len(batch))
# Применение
result = dfSample.select("rowid", col("value"), running_statistics(col("value")).alias("running_mean"))
result.limit(3).show(3)

+-----+-----+------------+
|rowid|value|running_mean|
+-----+-----+------------+
|    1|  1.0|         2.0|
|    2|  2.0|         2.0|
|    3|  3.0|         2.0|
+-----+-----+------------+



Обрабатывается батч размером: 3
running_sum = 6.0, running_count = 3


In [172]:
# Для 7 строк
result.show(6)

+-----+-----+------------+
|rowid|value|running_mean|
+-----+-----+------------+
|    1|  1.0|         4.0|
|    2|  2.0|         4.0|
|    3|  3.0|         4.0|
|    4|  4.0|         4.0|
|    5|  5.0|         4.0|
|    6|  6.0|         4.0|
+-----+-----+------------+
only showing top 6 rows



Обрабатывается батч размером: 7
running_sum = 28.0, running_count = 7


**Кэширование строк**

In [179]:
@pandas_udf("string")
def incremental_text_processing(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
    """Инкрементальная обработка текста с кэшем"""
    # Состояние: кэш обработанных значений
    processing_cache = {}
    processing_count = 0
    
    def expensive_text_operation(text):
        """Имитация дорогой операции обработки текста"""
        return text.upper().replace('A', '@').replace('E', '3')
    
    for batch in iterator:
        results = []
        
        for text in batch:
            if text in processing_cache:
                # Используем кэшированный результат
                result = processing_cache[text]
                print(f"From cache {processing_cache}")        
            else:
                # Выполняем дорогую операцию
                result = expensive_text_operation(text)
                processing_cache[text] = result
                processing_count += 1
            results.append(result)
        
        yield pd.Series(results)

# Данные с повторениями для демонстрации кэширования
text_data = [
    (1, "APACHE"), (2, "HIVE"), (3, "APACHE"),  # APACHE повторяется
    (4, "PYTHON"), (5, "HIVE"), (6, "SPARK")  # HIVE повторяется
]
df_text = spark.createDataFrame(text_data, ["id", "text"])

result = df_text.select("id", "text", incremental_text_processing(col("text")).alias("processed"))
result.show()

+---+------+---------+
| id|  text|processed|
+---+------+---------+
|  1|APACHE|   @P@CH3|
|  2|  HIVE|     HIV3|
|  3|APACHE|   @P@CH3|
|  4|PYTHON|   PYTHON|
|  5|  HIVE|     HIV3|
|  6| SPARK|    SP@RK|
+---+------+---------+



From cache {'APACHE': '@P@CH3', 'HIVE': 'HIV3'}


### 3. Обработка с внешними ресурсами
 - создается тестовая модель и сохраняется в фвйл
 - загружается модель и применяется (к батчам)

In [175]:
# Cоздаем и сохраняем модель
def create_and_save_model():
    """Создает и сохраняет модель в файл"""
    model_weights = [2.5, 1.3, 0.8]
    
    # Сохраняем в pickle файл
    with open('/tmp/model_weights.pkl', 'wb') as f:
        pickle.dump(model_weights, f)
    
    print("Модель сохранена в /tmp/model_weights.pkl")

# Создаем модель
create_and_save_model()

Модель сохранена в /tmp/model_weights.pkl


In [176]:
import pickle
import os

@pandas_udf("double")
def ml_prediction_batched(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
    """Применяет ML модель к батчам данных"""
    
    # Инициализация модели один раз для всех батчей
    # (имитация загрузки модели)
    model_path = '/tmp/model_weights.pkl'
    if os.path.exists(model_path):
        with open(model_path, 'rb') as f:
            model_weights = pickle.load(f)
        print(f"Модель загружена из {model_path}: {model_weights}")
    else:
        # Fallback модель, если файл не найден
        model_weights = [1.0, 0.0, 0.0]
        print("Файл модели не найден, используется fallback модель")
    
    for batch in iterator:
        # Применяем модель к каждому батчу
        predictions = batch * model_weights[0] + model_weights[1] + model_weights[2]
        yield predictions.round(5)

# Применение
result = dfSample.select("rowid", col("value"), ml_prediction_batched(col("value")).alias("prediction"))
result.show(10)

+-----+-----+----------+
|rowid|value|prediction|
+-----+-----+----------+
|    1|  1.0|       4.6|
|    2|  2.0|       7.1|
|    3|  3.0|       9.6|
|    4|  4.0|      12.1|
|    5|  5.0|      14.6|
|    6|  6.0|      17.1|
|    7|  7.0|      19.6|
|    8|  8.0|      22.1|
|    9|  9.0|      24.6|
|   10| 10.0|      27.1|
+-----+-----+----------+
only showing top 10 rows



Модель загружена из /tmp/model_weights.pkl: [2.5, 1.3, 0.8]


### 4. Обработка с несколькими колонками

In [178]:
@pandas_udf("double")
def complex_calculation_iter(
    iterator: Iterator[tuple[pd.Series, pd.Series]]
) -> Iterator[pd.Series]:
    """Сложные вычисления с несколькими входными колонками"""
    
    for value_batch, weight_batch in iterator:
        # Взвешенное преобразование
        result = (value_batch * weight_batch).apply(lambda x: x ** 0.5 if x > 0 else 0)
        yield result

# Данные с двумя колонками
data = [(i, float(i), float(i * 0.1)) for i in range(1, 101)]
df = spark.createDataFrame(data, ["id", "value", "weight"])

result = df.select(
    "id", 
    complex_calculation_iter(col("value"), col("weight")).alias("weighted_result")
)
result.show(10)

+---+-------------------+
| id|    weighted_result|
+---+-------------------+
|  1|0.31622776601683794|
|  2| 0.6324555320336759|
|  3| 0.9486832980505139|
|  4| 1.2649110640673518|
|  5| 1.5811388300841898|
|  6| 1.8973665961010278|
|  7| 2.2135943621178655|
|  8| 2.5298221281347035|
|  9| 2.8460498941515415|
| 10| 3.1622776601683795|
+---+-------------------+
only showing top 10 rows



### 5. Обработка текста с кэшированием

In [180]:
import re
from collections import defaultdict

@pandas_udf("string")
def text_processing_with_cache(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
    """Обработка текста с кэшированием результатов"""
    
    # Кэш для избежания повторных вычислений
    cache = {}
    
    def clean_text(text):
        if text in cache:
            return cache[text]
        
        if text is None:
            result = None
        else:
            # Сложная обработка текста
            result = re.sub(r'[^a-zA-Z0-9\s]', '', str(text)).strip().upper()
        
        cache[text] = result
        return result
    
    for batch in iterator:
        processed_batch = batch.apply(clean_text)
        yield processed_batch

# Тестовые текстовые данные
text_data = [
    (1, "Hello, World!"),
    (2, "Python Programming!!!"),
    (3, "Hello, World!"),  # Дублирование для демонстрации кэша
    (4, "Data Science & ML"),
    (5, "Python Programming!!!"),  # Еще один дубликат
] * 20  # Увеличиваем данные

df = spark.createDataFrame(text_data, ["id", "text"])

result = df.select("id", "text", text_processing_with_cache(col("text")).alias("cleaned"))
result.show(10, truncate=False)

+---+---------------------+------------------+
|id |text                 |cleaned           |
+---+---------------------+------------------+
|1  |Hello, World!        |HELLO WORLD       |
|2  |Python Programming!!!|PYTHON PROGRAMMING|
|3  |Hello, World!        |HELLO WORLD       |
|4  |Data Science & ML    |DATA SCIENCE  ML  |
|5  |Python Programming!!!|PYTHON PROGRAMMING|
|1  |Hello, World!        |HELLO WORLD       |
|2  |Python Programming!!!|PYTHON PROGRAMMING|
|3  |Hello, World!        |HELLO WORLD       |
|4  |Data Science & ML    |DATA SCIENCE  ML  |
|5  |Python Programming!!!|PYTHON PROGRAMMING|
+---+---------------------+------------------+
only showing top 10 rows



In [54]:
## 6. Обработка временных рядов
import numpy as np

@pandas_udf("double")
def sliding_window_stats(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
    """Вычисляет статистики скользящего окна между батчами"""
    
    window_buffer = []
    window_size = 5
    
    for batch in iterator:
        results = []
        
        for value in batch:
            window_buffer.append(value)
            
            # Поддерживаем размер окна
            if len(window_buffer) > window_size:
                window_buffer.pop(0)
            
            # Вычисляем среднее по окну
            window_mean = np.mean(window_buffer)
            results.append(window_mean)
        
        yield pd.Series(results)

# Временные ряды данных
ts_data = [(i, float(10 + 5 * np.sin(i * 0.1) + np.random.randn())) 
           for i in range(1, 201)]
df = spark.createDataFrame(ts_data, ["id", "value"])

result = df.select("id", "value", sliding_window_stats(col("value")).alias("smoothed"))
result.show(15)

+---+------------------+------------------+
| id|             value|          smoothed|
+---+------------------+------------------+
|  1|  8.72337438777616|  8.72337438777616|
|  2|11.312535971395075|10.017955179585616|
|  3|11.378671231810513|10.471527196993916|
|  4|11.670908106183157|10.771372424291226|
|  5|10.981005869540446| 10.81329911334107|
|  6|11.944485389294591|11.457521313644756|
|  7|12.610255667377583|11.717065252841257|
|  8|13.753010102738385|12.191933027026831|
|  9|13.802804380557463|12.618312281901694|
| 10|16.340010586236655|13.690113225240935|
| 11|13.411394555168805|13.983495058415775|
| 12|13.890326082693186|  14.2395091414789|
| 13|  16.2871305812955|14.746333237190322|
| 14|15.842454663212974|15.154263293721424|
| 15|14.990757958244792|14.884412768123052|
+---+------------------+------------------+
only showing top 15 rows



### 7. Сравнение производительности

In [181]:
import time

# Обычный SCALAR UDF
@pandas_udf("double")
def scalar_square(series: pd.Series) -> pd.Series:
    return series ** 2

# SCALAR_ITER UDF
@pandas_udf("double")
def scalar_iter_square(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
    for batch in iterator:
        yield batch ** 2

# Большой датасет
large_data = [(i, float(i)) for i in range(1, 200001)]
large_df = spark.createDataFrame(large_data, ["id", "value"])

# Тестирование SCALAR
start = time.time()
result1 = large_df.select("id", scalar_square(col("value")).alias("squared"))
count1 = result1.count()
scalar_time = time.time() - start

# Тестирование SCALAR_ITER
start = time.time()
result2 = large_df.select("id", scalar_iter_square(col("value")).alias("squared"))
count2 = result2.count()
scalar_iter_time = time.time() - start

print(f"SCALAR UDF time: {scalar_time:.2f} seconds")
print(f"SCALAR_ITER UDF time: {scalar_iter_time:.2f} seconds")

SCALAR UDF time: 0.15 seconds
SCALAR_ITER UDF time: 0.12 seconds


## Когда использовать SCALAR_ITER:

1. **Большие датасеты** - когда нужно контролировать использование памяти
2. **Статeful обработка** - когда нужно сохранять состояние между батчами
3. **Инициализация ресурсов** - когда дорого создавать объекты для каждого вызова
4. **Кэширование** - когда можно переиспользовать вычисления
5. **Потоковая обработка** - когда данные обрабатываются как поток

## Преимущества SCALAR_ITER:

- **Контроль памяти** - обрабатывает данные по частям
- **Эффективность** - можно переиспользовать дорогие объекты
- **Гибкость** - позволяет сохранять состояние между батчами

SCALAR_ITER особенно полезен для обработки больших объемов данных с ограниченной памятью

In [267]:
import pandas as pd
from typing import Iterator

# SCALAR - загружает все данные в память сразу
@pandas_udf("double")
def memoryintensivescalar(series: pd.Series) -> pd.Series:
    # Вся Series загружается в память одновременно
    print(f"Processing {len(series)} rows at once")
    return series ** 2

# SCALAR_ITER - обрабатывает данные батчами
@pandas_udf("double")
def memory_efficient_iter(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
    for i, batch in enumerate(iterator):
        # Каждый батч обрабатывается отдельно
        print(f"Processing batch {i} with {len(batch)} rows")
        yield batch ** 2

# Тест с большим датасетом
largedata = [(i, float(i)) for i in range(1, 22401)]  # 1M записей
df = spark.createDataFrame(largedata, ["id", "value"])

# SCALAR может вызвать OutOfMemory на больших данных
# SCALAR_ITER обработает по частям'''

In [269]:
df.withColumn("scalar_iter", memory_efficient_iter("value")).select("scalar_iter").show(200)

+-----------+
|scalar_iter|
+-----------+
|        1.0|
|        4.0|
|        9.0|
|       16.0|
|       25.0|
|       36.0|
|       49.0|
|       64.0|
|       81.0|
|      100.0|
|      121.0|
|      144.0|
|      169.0|
|      196.0|
|      225.0|
|      256.0|
|      289.0|
|      324.0|
|      361.0|
|      400.0|
|      441.0|
|      484.0|
|      529.0|
|      576.0|
|      625.0|
|      676.0|
|      729.0|
|      784.0|
|      841.0|
|      900.0|
|      961.0|
|     1024.0|
|     1089.0|
|     1156.0|
|     1225.0|
|     1296.0|
|     1369.0|
|     1444.0|
|     1521.0|
|     1600.0|
|     1681.0|
|     1764.0|
|     1849.0|
|     1936.0|
|     2025.0|
|     2116.0|
|     2209.0|
|     2304.0|
|     2401.0|
|     2500.0|
|     2601.0|
|     2704.0|
|     2809.0|
|     2916.0|
|     3025.0|
|     3136.0|
|     3249.0|
|     3364.0|
|     3481.0|
|     3600.0|
|     3721.0|
|     3844.0|
|     3969.0|
|     4096.0|
|     4225.0|
|     4356.0|
|     4489.0|
|     4624.0|
|     

Processing batch 0 with 201 rows
Exception ignored in: <_io.BufferedWriter name=5>
Traceback (most recent call last):
  File "/opt/spark/python/lib/pyspark.zip/pyspark/daemon.py", line 193, in manager
BrokenPipeError: [Errno 32] Broken pipe


In [270]:
df.withColumn("scalar", memoryintensivescalar("value")).show()

+---+-----+------+
| id|value|scalar|
+---+-----+------+
|  1|  1.0|   1.0|
|  2|  2.0|   4.0|
|  3|  3.0|   9.0|
|  4|  4.0|  16.0|
|  5|  5.0|  25.0|
|  6|  6.0|  36.0|
|  7|  7.0|  49.0|
|  8|  8.0|  64.0|
|  9|  9.0|  81.0|
| 10| 10.0| 100.0|
| 11| 11.0| 121.0|
| 12| 12.0| 144.0|
| 13| 13.0| 169.0|
| 14| 14.0| 196.0|
| 15| 15.0| 225.0|
| 16| 16.0| 256.0|
| 17| 17.0| 289.0|
| 18| 18.0| 324.0|
| 19| 19.0| 361.0|
| 20| 20.0| 400.0|
+---+-----+------+
only showing top 20 rows



Processing 21 rows at once
Exception ignored in: <_io.BufferedWriter name=5>
Traceback (most recent call last):
  File "/opt/spark/python/lib/pyspark.zip/pyspark/daemon.py", line 193, in manager
BrokenPipeError: [Errno 32] Broken pipe


In [82]:
### 3. **Сохранение состояния**

# SCALAR - НЕ может сохранять состояние между вызовами
@pandas_udf("double")
def scalarnostate(series: pd.Series) -> pd.Series:
    # Каждый вызов независим
    return series.cumsum()  # Работает только внутри текущей Series

# SCALARITER - МОЖЕТ сохранять состояние между батчами
@pandas_udf("double")
def scalariterwithstate(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
    runningsum = 0  # Состояние сохраняется между батчами
    
    for batch in iterator:
        # Продолжаем накопление с предыдущего батча
        cumulative = batch.cumsum() + runningsum
        runningsum += batch.sum()
        yield cumulative

# Демонстрация
data = (i, 1.0) for i in range(1, 21)
df = spark.createDataFrame(data, "id", "value")

result1 = df.select("id", scalarnostate(col("value")).alias("cumsumscalar"))
result2 = df.select("id", scalariterwithstate(col("value")).alias("cumsumiter"))

print("SCALAR (независимые батчи):")
result1.show()

print("SCALARITER (с состоянием):")
result2.show()

SyntaxError: invalid syntax (2180073242.py, line 21)

In [83]:

### 4. **Инициализация ресурсов**

In [85]:
import pickle
import time

# SCALAR - инициализация при каждом вызове (неэффективно)
@pandas_udf("double")
def scalarwithexpensiveinit(series: pd.Series) -> pd.Series:
    # Дорогая инициализация происходит каждый раз
    expensivemodel = loadmlmodel()  # Вызывается много раз!
    return series.apply(lambda x: expensivemodel.predict(x))

# SCALARITER - инициализация один раз (эффективно)
@pandas_udf("double")
def scalariterefficientinit(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
    # Дорогая инициализация происходит только один раз
    expensivemodel = loadmlmodel()  # Вызывается один раз!
    
    for batch in iterator:
        predictions = batch.apply(lambda x: expensivemodel.predict(x))
        yield predictions

def loadmlmodel():
    """Имитация загрузки тяжелой ML модели"""
    print("Loading expensive ML model...")
    time.sleep(1)  # Имитация долгой загрузки
    return {"weights": [1.5, 2.0, 0.5]}  # Простая модель

In [87]:
### 5. **Обработка ошибок**

# SCALAR - ошибка влияет на всю partition
@pandas_udf("double")
def scalarerrorprone(series: pd.Series) -> pd.Series:
    # Если ошибка - вся partition падает
    return series.apply(lambda x: 1/x if x != 0 else float('inf'))

# SCALARITER - можно обработать ошибки по батчам
@pandas_udf("double")
def scalaritererrorhandling(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
    for batchnum, batch in enumerate(iterator):
        try:
            result = batch.apply(lambda x: 1/x if x != 0 else float('inf'))
            yield result
        except Exception as e:
            print(f"Error in batch {batch_num}: {e}")
            # Возвращаем безопасные значения
            yield pd.Series([0.0] * len(batch))

In [89]:
### 6. **Практический пример - кэширование**

# SCALAR_ITER с кэшированием (эффективно)
@pandas_udf("string")
def cached_text_processing(iterator: Iterator[pd.Series]) -> Iterator[pd.Series]:
    cache = {}  # Кэш живет между всеми батчами
    
    def process_text(text):
        if text in cache:
            return cache[text]
        
        # Дорогая обработка
        result = text.upper().strip() if text else None
        cache[text] = result
        return result
    
    for batch in iterator:
        processed = batch.apply(process_text)
        yield processed

In [182]:
# SCALAR без кэширования (неэффективно для повторяющихся данных)
@pandas_udf("string")
def uncached_text_processing(series: pd.Series) -> pd.Series:
    # Кэш пересоздается для каждого вызова
    def process_text(text):
        return text.upper().strip() if text else None
    
    return series.apply(process_text)

## Сравнительная таблица:
| Характеристика | SCALAR | SCALAR_ITER |
|---------------|---------|-------------|
| **Память** | Загружает всю partition | Обрабатывает батчами |
| **Состояние** | Не сохраняется | Сохраняется между батчами |
| **Инициализация** | При каждом вызове | Один раз на partition |
| **Производительность** | Быстрее для малых данных | Лучше для больших данных |
| **Сложность** | Проще в реализации | Требует понимания итераторов |
| **Кэширование** | Ограниченное | Эффективное |

In [20]:
spark.stop()